# Final Code for Extractive Based Summary

## Code for Extractive Type

In [10]:
## Importing required packages...
import nltk
import string
import os
import networkx as nx
from nltk.wsd import lesk
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize,RegexpTokenizer,sent_tokenize
from nltk.corpus import wordnet,stopwords
from string import punctuation
from inspect import getsourcefile
from collections import defaultdict
from os.path import abspath,join,dirname
from heapq import nlargest
import time
import matplotlib.pyplot as plt
# import logging
# logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
# #from nltk.corpus import wordnet as wn
stop_words = set(stopwords.words('english'))

In [57]:
## List of Relations of each nouns...
def relation_list(nouns):
    relation_list= defaultdict(list)
    for x in range(len(nouns)):
        relation=[]
        for syns in wordnet.synsets(nouns[x],pos=wordnet.NOUN):
            for lema in syns.lemmas():
                relation.append(lema.name())
                if lema.antonyms():
                    relation.append(lema.antonyms()[0].name())
            for hypnyms in syns.hypernyms():
                if hypnyms.hypernyms():
                    relation.append(hypnyms.hypernyms()[0].name().split('.')[0])
        relation_list[nouns[x]].append(relation)
    #for each in relation_list:
    print("\n_______________")
    print("\n Relation List")
    print("\n ",relation_list)
    print("\n_______________")
    return relation_list

In [58]:
## Computing LC to Nouns and their relations...
##Also applying threshold of similarity..
def LC(nouns, relation_list):
    lexical=[]
    threshold=0.5
    for noun in nouns:
        flag=0
        for lex in range(len(lexical)):
            if flag==0:
                for keys in list(lexical[lex]):
                    if keys == noun and flag==0:
                        lexical[lex][noun]+=1
                        flag=1
                    elif keys in relation_list[noun][0] and flag==0:
                        syn1=wordnet.synsets(keys,pos=wordnet.NOUN)
                        syn2=wordnet.synsets(noun,pos=wordnet.NOUN)
                        if syn1[0].wup_similarity(syn2[0]) >=threshold:
                            lexical[lex][noun]=1
                            flag=1
        if flag==0:
            dic_nuevo={}
            dic_nuevo[noun]=1
            lexical.append(dic_nuevo)
            flag=1
    print("\nLexical ",lexical)
    print("\n_______________")
    return lexical

In [59]:
## Pruning the LC, by deleting the chains which are weak...
def Prune(lexical):
    chain_final=[]
    while lexical:
        reslt=lexical.pop()
        if len(reslt.keys())==1:
            for values in reslt.values():
                if values!=1:
                    chain_final.append(reslt)
        else:
            chain_final.append(reslt)
    print("\n Final Chain")
    print("\n ",chain_final)
    print("\n_______________")
    return chain_final

In [60]:
## Summary class...
class Summary:
    def __init__(self,thld_min=.1,thld_max=0.9):
        self.thld_min=thld_min
        self.thld_max=thld_max
        self._stopwords=set(stopwords.words('english')+list(punctuation));
    ##Calculate freq of every word in the document, along with the LC...  
    def frequency(self,words,LC):
        freq=defaultdict(int)
        for wrd in words:
            for w in wrd:
                if w not in self._stopwords:
                    flag=0
                    for i in LC:
                        if w in list(i.keys()):
                            freq[w]=sum(list(i.values()))
                            flag=1
                            break
                    if flag==0:
                        freq[w]+=1
        mx=float(max(freq.values()))
        for w in list(freq.keys()):
            freq[w]=freq[w]/mx
            if freq[w]>=self.thld_max or freq[w]<=self.thld_min:
                del freq[w]
       # print("freq ",freq)
        return freq
    
    ##Final Summary using heap of important sentences...
    def summarize(self,statements,LC,size):
        assert size<= len(statements)
        wrd_statements=[word_tokenize(s.lower()) for s in statements]
        self.freq=self.frequency(wrd_statements,LC)
        Rank=defaultdict(int)
        for i,stmt in enumerate(wrd_statements):
            for words in stmt:
                if words in self.freq:
                    Rank[i]+=self.freq[words]
                    index=self.rank(Rank,size)
        final_index=sorted(index)
        #z=(statements[j] for j in final_index)
        #print("z ",z)
        return[statements[j] for j in final_index]
        
    ##Creating Heap of best sentences and returning it...
    def rank(self,Rank,size):
        return nlargest(size,Rank,key=Rank.get)

In [61]:
##Keeping all the text files in a list for process...
data=[]
import glob
for list_o_file in glob.iglob('**/*.txt', recursive=True):
    print(list_o_file)
    data.append(list_o_file)
#print(data)
data_len=len(data)

input.txt
News Articles\tech\001.txt
News Articles\tech\002.txt
News Articles\tech\003.txt
News Articles\tech\004.txt
News Articles\tech\005.txt
News Articles\tech\006.txt
News Articles\tech\007.txt
News Articles\tech\008.txt
News Articles\tech\009.txt
News Articles\tech\010.txt
News Articles\tech\011.txt
News Articles\tech\012.txt
News Articles\tech\013.txt
News Articles\tech\014.txt
News Articles\tech\015.txt
News Articles\tech\016.txt
News Articles\tech\017.txt
News Articles\tech\018.txt
News Articles\tech\019.txt
News Articles\tech\020.txt
News Articles\tech\021.txt
News Articles\tech\022.txt
News Articles\tech\023.txt
News Articles\tech\024.txt
News Articles\tech\025.txt
News Articles\tech\026.txt
News Articles\tech\027.txt
News Articles\tech\028.txt
News Articles\tech\029.txt
News Articles\tech\030.txt
News Articles\tech\031.txt
News Articles\tech\032.txt
News Articles\tech\033.txt
News Articles\tech\034.txt
News Articles\tech\035.txt
News Articles\tech\036.txt
News Articles\tech

In [62]:
print("\nTotal count of text files available are:",data_len)


Total count of text files available are: 201


In [63]:
##Main class...
start1 = time.time()
if __name__=="__main__":
    ##I/P file...
    for everyfile in data:
        start = time.time()
        ip=everyfile#join(dirname(abspath(getsourcefile(lambda:0))),"*.txt")
        with open(ip,"r",encoding="utf-8") as op:
            Input_text=op.read()
            op.close()
        print("The input File is:\n")
        print(Input_text)
        ##Provides the Nouns, Adverbs, Adjectives for the whole document...
        posit=['NN','NNS','NNP','NNPS','RB','JJ','VB']
        sent=nltk.sent_tokenize(Input_text)
        tokenizer=RegexpTokenizer(r'\w+')
        tokens=[tokenizer.tokenize(w) for w in sent]
        tagged=[pos_tag(tok) for tok in tokens]
        nouns=[word.lower() for i in range(len(tagged)) for word, pos in tagged[i] if pos in posit]
        relation=relation_list(nouns)
        lexical=LC(nouns, relation)
        chain_final=Prune(lexical)

        ##Printing the LC...
        print("\n Printing the LC")
        for i in range(len(chain_final)):
            x="Chain"+str(i+1)+":"+str(chain_final[i])
            print("\n ",x)
        
        ##Summarizing the ip...
        if len(sent)>=5:
            size=5
        else:
            size=5
        F_S=Summary()
        print("\n_______________")
        print("\n The Summarized data for the above txt is:\n")
        print(F_S.summarize(sent,chain_final,size))
        print("\n*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*")        
        n=0
        if n<=len(data):
            file=open(os.path.join('Output for Extractive', os.path.basename(everyfile)) , 'w')
            #file = open('Output for Extractive\summaryoutput.txt',n, 'w')
            for s in F_S.summarize(sent,chain_final,size):
                file.write(s) 
            file.close()
        end = time.time()
        print(f"\n Runtime of the above Summary is : {end - start} seconds")
        print("\n*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*")
# Total Time Taken...
end1 = time.time()
print(f"Total Runtime of the program is : {end1 - start1} seconds")

The input File is:

﻿We observe today not a victory of party but a celebration of freedom--symbolizing an end as well as a beginning--signifying renewal as well as change. For I have sworn before you and Almighty God the same solemn oath our for bears prescribed nearly a century and three-quarters ago. The world is very different now. For man holds in his mortal hands the power to abolish all forms of human poverty and all forms of human life. And yet the same revolutionary beliefs for which our forebears fought are still at issue around the globe--the belief that the rights of man come not from the generosity of the state but from the hand of God. We dare not forget today that we are the heirs of that first revolution. Let the word go forth from this time and place, to friend and foe alike, that the torch has been passed to a new generation of Americans--born in this century, tempered by war, disciplined by a hard and bitter peace, proud of our ancient heritage--and unwilling to witne


Lexical  [{'today': 3}, {'not': 19}, {'victory': 1}, {'party': 1}, {'celebration': 1}, {'freedom': 4, 'liberty': 1}, {'end': 1}, {'as': 2}, {'well': 3}, {'beginning': 1}, {'renewal': 1}, {'change': 1, 'undoing': 1, 'break': 1}, {'almighty': 1}, {'god': 3}, {'same': 3}, {'solemn': 1}, {'bears': 1}, {'nearly': 1}, {'century': 2}, {'quarters': 1}, {'ago': 1}, {'world': 8, 'man': 1, 'human': 1, 'globe': 1, 'mankind': 1, 'earth': 1}, {'very': 1}, {'different': 1}, {'now': 2}, {'mortal': 1}, {'power': 5, 'powers': 1}, {'abolish': 1}, {'forms': 2}, {'poverty': 3}, {'life': 3}, {'yet': 2}, {'revolutionary': 1}, {'beliefs': 1}, {'forebears': 1}, {'still': 1}, {'issue': 1}, {'belief': 1}, {'rights': 2}, {'generosity': 1}, {'state': 1, 'place': 1, 'home': 1, 'states': 1, 'places': 1}, {'hand': 2}, {'forget': 1}, {'heirs': 1}, {'first': 4}, {'revolution': 2}, {'let': 16}, {'word': 2}, {'go': 2}, {'forth': 2}, {'time': 2}, {'friend': 2, 'foe': 1, 'friends': 1}, {'alike': 1}, {'torch': 1}, {'new': 


_______________

 The Summarized data for the above txt is:

['Let the word go forth from this time and place, to friend and foe alike, that the torch has been passed to a new generation of Americans--born in this century, tempered by war, disciplined by a hard and bitter peace, proud of our ancient heritage--and unwilling to witness or permit the slow undoing of those human rights to which this nation has always been committed, and to which we are committed today at home and around the world.', 'Let every nation know, whether it wishes us well or ill, that we shall pay any price, bear any burden, meet any hardship, support any friend, oppose any foe to assure the survival and the success of liberty.', 'And if a beachhead of cooperation may push back the jungle of suspicion, let both sides join in creating a new endeavor, not a new balance of power, but a new world of law, where the strong are just and the weak secure and the peace preserved.', 'Now the trumpet summons us again--not a


 Final Chain

  [{'serbia': 2}, {'type': 3}, {'forward': 3}, {'move': 1, 'step': 1}, {'non': 2}, {'problems': 3}, {'such': 2}, {'society': 1, 'societies': 1}, {'common': 2}, {'widely': 2}, {'other': 3}, {'as': 2}, {'even': 2}, {'be': 3}, {'enter': 2}, {'voter': 4}, {'election': 3}, {'station': 2}, {'however': 2}, {'light': 3}, {'visible': 2}, {'thumb': 3}, {'person': 1, 'official': 1, 'sheep': 1, 'author': 1, 'christian': 1}, {'not': 7}, {'ballot': 3}, {'towards': 2}, {'many': 2}, {'government': 3, 'regime': 1}, {'presidential': 2}, {'parliamentary': 3}, {'upcoming': 2}, {'use': 9}, {'law': 2}, {'population': 1, 'populations': 1}, {'technology': 2}, {'part': 3}, {'elections': 12}, {'s': 3}, {'country': 2, 'countries': 1}, {'readers': 3}, {'ultraviolet': 3, 'uv': 1}, {'invisible': 2}, {'soviet': 2}, {'former': 2}, {'republic': 3, 'republics': 1}, {'kyrgyz': 4}, {'democracy': 2}, {'drive': 3, 'effort': 1, 'cause': 1}, {'ink': 23}]

_______________

 Printing the LC

  Chain1:{'serbia': 


  Chain1:{'group': 1, 'mail': 1}

  Chain2:{'sites': 2}

  Chain3:{'time': 2}

  Chain4:{'not': 2}

  Chain5:{'computer': 2, 'pcs': 1}

  Chain6:{'also': 3}

  Chain7:{'hours': 2}

  Chain8:{'people': 8}

  Chain9:{'young': 2}

  Chain10:{'use': 4, 'technologies': 1}

  Chain11:{'schools': 2}

  Chain12:{'be': 3}

  Chain13:{'rules': 2}

  Chain14:{'guidelines': 2}

  Chain15:{'strict': 2}

  Chain16:{'operate': 2}

  Chain17:{'down': 2}

  Chain18:{'agency': 2}

  Chain19:{'news': 2}

  Chain20:{'official': 2}

  Chain21:{'country': 2}

  Chain22:{'months': 2}

  Chain23:{'authorities': 3, 'government': 1}

  Chain24:{'chinese': 6}

  Chain25:{'crackdown': 4}

  Chain26:{'cafe': 3, 'cafes': 1}

  Chain27:{'net': 15}

  Chain28:{'china': 5}

_______________

 The Summarized data for the above txt is:

["China net cafe culture crackdown\n\nChinese authorities closed 12,575 net cafes in the closing months of 2004, the country's government said.", 'The official Xinhua News Agency said th

...


_______________

 Relation List

  defaultdict(<class 'list'>, {'smartphones': [[], []], 'skulls': [['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue'], ['skull', 'connective_tissue']], 'attack': [['attack', 'onslaught', 'onset', 'onrush', 'activity', 'attack', 'activity', 'fire', 'attack', 'flak', 'flack', 'blast', 'disapproval', 'approach', 'attack', 'plan_of_attack', 'creating_by_mental_acts', 'attack', 'attempt', 'transgression', 'attack', 'tone-beginning', 'change_of_state', 'attack', 'trouble', 'attack', 'process', 'attack', 'disapproval'], ['attack', 'onslaught', 'onset', 'onrush', 'activity', 'attack', 'activity', 'fire', 'attack', 'flak', 'flack', 'blast', 'disapproval', 'approach', 'attack', 'plan_of_attack', 'creating_by_mental_acts', 'attack', 'attempt', 'transgression', 'a


_______________

 Relation List

  defaultdict(<class 'list'>, {'musical': [['musical', 'musical_comedy', 'musical_theater', 'product', 'show']], 'future': [['future', 'past', 'hereafter', 'futurity', 'time_to_come', 'attribute', 'future', 'future_tense', 'grammatical_category', 'future', 'artifact'], ['future', 'past', 'hereafter', 'futurity', 'time_to_come', 'attribute', 'future', 'future_tense', 'grammatical_category', 'future', 'artifact']], 'phones': [['telephone', 'phone', 'telephone_set', 'equipment', 'phone', 'speech_sound', 'sound', 'part', 'earphone', 'earpiece', 'headphone', 'phone', 'transducer'], ['telephone', 'phone', 'telephone_set', 'equipment', 'phone', 'speech_sound', 'sound', 'part', 'earphone', 'earpiece', 'headphone', 'phone', 'transducer'], ['telephone', 'phone', 'telephone_set', 'equipment', 'phone', 'speech_sound', 'sound', 'part', 'earphone', 'earpiece', 'headphone', 'phone', 'transducer'], ['telephone', 'phone', 'telephone_set', 'equipment', 'phone', 'speech_

The input File is:

Multi-purpose TV aids India

Two-thirds of the world's population, 4 billion people, live on $2,000 a year or less.

You might think that the last thing on their minds would be getting a television set or a computer. But that's not the case. Many people in the developing world give up one of their daily meals so they can afford to buy a TV. And now, an Indian-born computer engineer thinks he's come up with a way to give them cheap access to the internet. Carnegie Mellon Professor Raj Reddy has spent the bulk of his professional career trying to find ways to make technology accessible to poor people. The first step is to figure out why poor people would want a personal computer and Professor Reddy thinks he has a pretty good idea of why they might. "I come from a village," says Prof Reddy, "I know what the population is like, many of them are illiterate, and many of them have other concerns." "There, nobody will use it for the conventional uses of a PC, word processi

The input File is:

Computer grid to help the world

Your computer can now help solve the world's most difficult health and social problems.

Launched this week, the World Community Grid will use idle computer time to test solutions to these problems. The donated processor cycles will help the WCG create virtual supercomputers via the net. The idea follows the success of other similar projects that have used the untapped processing power of millions of desktop PCs. One of the most successful collaboration projects was Seti@home, run by the Search for Extra Terrestrial Life project, which sorted through radio signals looking for signs of alien communication.

Anyone can volunteer to donate the spare time of their computers by downloading a special screensaver from the WGC website. Once installed, the virtual terminal gets a chunk of the computational task to process, and reports back after completing that task. The first WCG problem being tackled will be the Human Proteome Folding Proje

Lexical  [{'computer': 4, 'pcs': 1, 'computers': 1}, {'grid': 5}, {'help': 4, 'services': 1}, {'world': 5, 'globe': 1}, {'now': 1}, {'solve': 1}, {'difficult': 1}, {'health': 3}, {'social': 1}, {'problems': 3}, {'week': 1}, {'community': 2}, {'use': 1, 'technology': 1}, {'idle': 1}, {'time': 2}, {'test': 1}, {'solutions': 1}, {'processor': 1}, {'cycles': 1}, {'wcg': 2}, {'virtual': 2}, {'supercomputers': 1}, {'net': 1}, {'idea': 1}, {'success': 1}, {'other': 1}, {'similar': 1}, {'projects': 3}, {'untapped': 1}, {'power': 1}, {'millions': 1}, {'desktop': 1}, {'successful': 1}, {'collaboration': 1}, {'seti': 1}, {'home': 1}, {'run': 1}, {'search': 2}, {'extra': 1}, {'terrestrial': 1}, {'life': 1}, {'project': 2, 'task': 1}, {'radio': 1}, {'signals': 1}, {'signs': 1}, {'alien': 1}, {'communication': 1, 'analysis': 1}, {'anyone': 1}, {'volunteer': 1, 'volunteers': 1}, {'donate': 1}, {'spare': 1}, {'special': 1}, {'screensaver': 1}, {'wgc': 1}, {'website': 1}, {'once': 1}, {'terminal': 1}, 

## Rouge Test

In [64]:
## Evaluations of Text Summaries...
import os
import time
from os.path import abspath,join,dirname
from inspect import getsourcefile
ip=join(dirname(abspath(getsourcefile(lambda:0))),"input.txt")#r"News Articles\business\002.txt")
with open(ip,"r",encoding="utf-8") as op:
    Input_text=op.read()
    op.close()    
print("The Input text file:\n",Input_text)
print("\nThe count of words:\n",len(Input_text))
print("________________")

opt=join(dirname(abspath(getsourcefile(lambda:0))),r"Output for Extractive\input.txt")
with open(opt,"r",encoding="utf-8") as opx:
    Output_text=opx.read()
    opx.close()
print("The Output text file:\n",Output_text)
print("\nThe count of words:\n",len(Output_text))

The Input text file:
 ﻿We observe today not a victory of party but a celebration of freedom--symbolizing an end as well as a beginning--signifying renewal as well as change. For I have sworn before you and Almighty God the same solemn oath our for bears prescribed nearly a century and three-quarters ago. The world is very different now. For man holds in his mortal hands the power to abolish all forms of human poverty and all forms of human life. And yet the same revolutionary beliefs for which our forebears fought are still at issue around the globe--the belief that the rights of man come not from the generosity of the state but from the hand of God. We dare not forget today that we are the heirs of that first revolution. Let the word go forth from this time and place, to friend and foe alike, that the torch has been passed to a new generation of Americans--born in this century, tempered by war, disciplined by a hard and bitter peace, proud of our ancient heritage--and unwilling to wit

In [55]:
#Applying ROUGE Score Test...
import rouge

def prepare_results(p, r, f):
    return '\t{}:\t{}: {:5.2f}\t{}: {:5.2f}\t{}: {:5.2f}'.format(metric, 'P', 100.0 * p, 'R', 100.0 * r, 'F1', 100.0 * f)


for aggregator in ['Best']:#['Avg', 'Best', 'Individual']:
    print('Evaluation with {}'.format(aggregator))
    apply_avg = aggregator == 'Avg'
    apply_best = aggregator == 'Best'

    evaluator = rouge.Rouge(metrics=['rouge-n', 'rouge-l', 'rouge-w'],
                           max_n=3,
                           limit_length=True,
                           length_limit=500,
                           length_limit_type='words',
                           apply_avg=apply_avg,
                           apply_best=apply_best,
                           alpha=0.5, # Default F1_score
                           weight_factor=1.2,
                           stemming=True)
    hypothesis_1 = Output_text
    references_1 = [Input_text]
    scores = evaluator.get_scores(hypothesis_1, references_1)
    for metric, results in sorted(scores.items(), key=lambda x: x[0]):
        if not apply_avg and not apply_best: # value is a type of list as we evaluate each summary vs each reference
            for hypothesis_id, results_per_ref in enumerate(results):
                nb_references = len(results_per_ref['p'])
                for reference_id in range(nb_references):
                    print('\tHypothesis #{} & Reference #{}: '.format(hypothesis_id, reference_id))
                    print( ''+ prepare_results(results_per_ref['p'][reference_id], results_per_ref['r'][reference_id], results_per_ref['f'][reference_id]))
            print()
        else:
            print(prepare_results(results['p'], results['r'], results['f']))
    print()

Evaluation with Best
	rouge-1:	P: 37.82	R: 23.58	F1: 29.05
	rouge-2:	P:  1.09	R:  0.68	F1:  0.84
	rouge-3:	P:  0.00	R:  0.00	F1:  0.00
	rouge-l:	P: 32.73	R: 22.08	F1: 26.37
	rouge-w:	P: 13.49	R:  3.37	F1:  5.39



In [11]:
##Backup

In [46]:
# ##Main class
# start = time.time()

# if __name__=="__main__":
    
#     ##I/P file
#     ip=join(dirname(abspath(getsourcefile(lambda:0))),"input.txt")
#     with open(ip,"r",encoding="utf-8") as op:
#         Input_text=op.read()
#         op.close()
#     print(Input_text)
        
#     ##Provides the Nouns, Adverbs, Adjectives for the whole document.
#     posit=['NN','NNS','NNP','NNPS','RB','JJ']
#     sent=nltk.sent_tokenize(Input_text)
#     tokenizer=RegexpTokenizer(r'\w+')
#     tokens=[tokenizer.tokenize(w) for w in sent]
#     tagged=[pos_tag(tok) for tok in tokens]
#     nouns=[word.lower() for i in range(len(tagged)) for word, pos in tagged[i] if pos in posit]
#     relation=relation_list(nouns)
#     lexical=LC(nouns, relation)
#     chain_final=Prune(lexical)
    
#     ##Printing the LC...
#     print("\n Printing the LC")
#     for i in range(len(chain_final)):
#         x="Chain"+str(i+1)+":"+str(chain_final[i])
#         print("\n ",x)

# end = time.time()

# # total time taken
# print(f"Runtime of the program is : {end - start} seconds")

In [47]:
# ##Size of Statements required, So based on the size summary is given out...
# if len(sent)>=5:
#     size=5
# else:
#     size=5
# F_S=Summary()
# print(F_S.summarize(sent,chain_final,size))

# file = open('Output for Extractive\summaryoutput.txt', 'w')
# for s in F_S.summarize(sent,chain_final,size):
#     file.write(s) 
# file.close()

In [14]:
# """#Rouge score Test for the Summarization
# from rouge import FilesRouge
# files_rouge = FilesRouge()
# scores = files_rouge.get_scores(r'C:\Users\user\Desktop\Mtech Projects\Summarization Project Code\TRAILS\Output for Extractive\summaryoutput.txt',r'C:\Users\user\Desktop\Mtech Projects\Summarization Project Code\TRAILS\input.txt')
# #print("\n ",scores)"""

In [15]:
## Count of files

In [16]:
# import os
# directory = r'C:\Users\user\Desktop\Mtech Projects\Summarization Project Code\Data\BBC News Summary\News Articles\business'

# number_of_files = len([item for item in os.listdir(directory) if os.path.isfile(os.path.join(directory, item))])
# number_of_files

In [17]:
# def getListOfFiles(dirName):
#     # create a list of file and sub directories 
#     # names in the given directory 
#     listOfFile = os.listdir(dirName)
#     allFiles = list()
#     # Iterate over all the entries
#     for entry in listOfFile:
#         # Create full path
#         fullPath = os.path.join(dirName, entry)
#         # If entry is a directory then get the list of files in this directory 
#         if os.path.isdir(fullPath):
#             allFiles = allFiles + getListOfFiles(fullPath)
#         else:
#             allFiles.append(fullPath)
                
#     return allFiles

In [18]:
# #a=os.listdir(path=r'C:\Users\user\Desktop\Mtech Projects\Summarization Project Code\Data\BBC News Summary\News Articles')

# dirName = r'C:\Users\user\Desktop\Mtech Projects\Summarization Project Code\Data\BBC News Summary\News Articles';
# Bdir=dirName+r'\business'
# Edir=dirName+r'\entertainment'
# Pdir=dirName+r'\politics'
# Sdir=dirName+r'\sport'
# Tdir=dirName+r'\tech'
# dir=['Bdir','Edir','Pdir','Sdir','Tdir']
# l=(len(dir))
# a=Bdir;b=Edir;c=Pdir;d=Sdir;e=Tdir;
# # Get the list of all files in directory tree at given path
# listOfFiles = getListOfFiles(a)
# leng1=len(listOfFiles)
# print("Business:",leng1)
# listOfFiles = getListOfFiles(b)
# leng2=len(listOfFiles)
# print("Entertainment:",leng2)
# listOfFiles = getListOfFiles(c)
# leng3=len(listOfFiles)
# print("Politics:",leng3)
# listOfFiles = getListOfFiles(d)
# leng4=len(listOfFiles)
# print("Sports:",leng4)
# listOfFiles = getListOfFiles(e)
# leng5=len(listOfFiles)
# print("Technology:",leng5)
# total=leng1+leng2+leng3+leng4+leng5
# print("Total count is:",total)

In [19]:
# ##Display the count of files...
# import matplotlib.pyplot as plt
# import pandas as pd
# fig = plt.figure()
# ax = fig.add_axes([0,0,1,1])
# langs = ['Business', 'Entertainment', 'Politics', 'Sports', 'Technology']
# students = [leng1,leng2,leng3,leng4,leng5]
# ax.bar(langs,students,color='green')
# ax.set_xlabel('Folders',fontsize=18)
# ax.set_ylabel('Count',fontsize=18)
# ax.set_title('Display of Count of Text Files in Dataset',fontsize=18)
# label=['510','386','417','511','401']
# for i in ax.patches:
#     # get_x pulls left or right; get_height pushes up or down
#     ax.text(i.get_x()+.04, i.get_height()+2, \
#             str(round((i.get_height()), 2)), fontsize=12, color='black')
# #ax.set_xticklabels(label)
# plt.show()